# Exploratory Data Analysis (EDA) for Telco Customer Churn

This notebook performs a comprehensive exploratory data analysis on the Telco Customer Churn dataset to understand its structure, feature distributions, relationships, and interactions. The goal is to identify key churn drivers, analyze feature interactions, and provide insights for feature selection and engineering in model development.

## Objectives
- Summarize dataset structure and quality.
- Analyze feature distributions and relationships with churn.
- Test as many feature interactions as possible (e.g., `InternetService` and `MonthlyCharges`).
- Use diverse visualizations (3D scatter plots, grouped bar plots, heatmaps, etc.).
- Apply statistical tests to quantify relationships.
- Recommend features and engineering steps for model development.

## Dataset
- **Source**: `Data/telco_customer_churn.csv`
- **Features**: 21 (e.g., `gender`, `tenure`, `Contract`, `MonthlyCharges`, `Churn`)
- **Target**: `Churn` (Yes/No)

## Tools
- Pandas, NumPy: Data manipulation
- Matplotlib, Seaborn: Static visualizations
- Plotly: Interactive visualizations
- SciPy, Statsmodels: Statistical tests
- Scikit-learn: Feature importance


## 1. Import Libraries

In [ ]:
import pandas as pd # type: ignore
import numpy as np # type: ignore
import matplotlib.pyplot as plt # type: ignore
import seaborn as sns # type: ignore
import plotly.express as px # type: ignore
import plotly.graph_objects as go # type: ignore
from scipy import stats # type: ignore
from statsmodels.stats.multicomp import pairwise_tukeyhsd # type: ignore
from sklearn.ensemble import RandomForestClassifier # type: ignore
from sklearn.preprocessing import LabelEncoder # type: ignore
import warnings
warnings.filterwarnings('ignore')

%matplotlib inline
sns.set_style('whitegrid')
plt.rcParams['figure.figsize'] = (10, 6)

## 2. Load and Inspect Dataset


In [2]:
# Load dataset
df = pd.read_csv('Data/telco_customer_churn.csv')

# Display basic info
print("Dataset Shape:", df.shape)
print("\nColumns and Data Types:")
print(df.dtypes)
print("\nFirst 5 Rows:")
display(df.head())

# Check missing values
print("\nMissing Values:")
print(df.isnull().sum())

# Check duplicates
print("\nNumber of Duplicates:", df.duplicated().sum())


Dataset Shape: (7043, 21)

Columns and Data Types:
customerID           object
gender               object
SeniorCitizen         int64
Partner              object
Dependents           object
tenure                int64
PhoneService         object
MultipleLines        object
InternetService      object
OnlineSecurity       object
OnlineBackup         object
DeviceProtection     object
TechSupport          object
StreamingTV          object
StreamingMovies      object
Contract             object
PaperlessBilling     object
PaymentMethod        object
MonthlyCharges      float64
TotalCharges         object
Churn                object
dtype: object

First 5 Rows:


customerID  gender  SeniorCitizen Partner Dependents  tenure PhoneService  \
0  7590-VHVEG  Female              0     Yes         No       1           No   
1  5575-GNVDE    Male              0      No         No      34          Yes   
2  3668-QPYBK    Male              0      No         No       2          Yes   
3  7795-CFOCW    Male              0      No         No      45           No   
4  9237-HQITU  Female              0      No         No       2          Yes   

      MultipleLines InternetService OnlineSecurity  ... DeviceProtection  \
0  No phone service             DSL             No  ...               No   
1                No             DSL            Yes  ...              Yes   
2                No             DSL            Yes  ...               No   
3  No phone service             DSL            Yes  ...              Yes   
4                No     Fiber optic             No  ...               No   

  TechSupport StreamingTV StreamingMovies        Contract PaperlessBilling  \
0          No          No              No  Month-to-month              Yes   
1          No          No              No        One year               No   
2          No          No              No  Month-to-month              Yes   
3         Yes          No              No        One year               No   
4          No          No              No  Month-to-month              Yes   

               PaymentMethod MonthlyCharges  TotalCharges Churn  
0           Electronic check          29.85         29.85    No  
1               Mailed check          56.95        1889.5    No  
2               Mailed check          53.85        108.15   Yes  
3  Bank transfer (automatic)          42.30       1840.75    No  
4           Electronic check          70.70        151.65   Yes  

[5 rows x 21 columns]


Missing Values:
customerID          0
gender              0
SeniorCitizen       0
Partner             0
Dependents          0
tenure              0
PhoneService        0
MultipleLines       0
InternetService     0
OnlineSecurity      0
OnlineBackup        0
DeviceProtection    0
TechSupport         0
StreamingTV         0
StreamingMovies     0
Contract            0
PaperlessBilling    0
PaymentMethod       0
MonthlyCharges      0
TotalCharges        0
Churn               0
dtype: int64

Number of Duplicates: 0


## 3. Data Cleaning

In [3]:
# Convert TotalCharges to numeric, handle empty strings
df['TotalCharges'] = pd.to_numeric(df['TotalCharges'], errors='coerce')
print("\nMissing TotalCharges after conversion:", df['TotalCharges'].isnull().sum())

# Impute missing TotalCharges with median for new customers (tenure=0)
df.loc[(df['TotalCharges'].isnull()) & (df['tenure'] == 0), 'TotalCharges'] = 0
df['TotalCharges'].fillna(df['TotalCharges'].median(), inplace=True)

# Remove duplicates if any
df = df.drop_duplicates()

# Standardize categorical values
for col in ['MultipleLines', 'OnlineSecurity', 'OnlineBackup', 'DeviceProtection', 'TechSupport', 'StreamingTV', 'StreamingMovies']:
    df[col] = df[col].replace({'No phone service': 'No', 'No internet service': 'No'})

# Verify cleaning
print("\nMissing Values after Cleaning:")
print(df.isnull().sum())
print("\nDataset Shape after Cleaning:", df.shape)
print("\nFirst 5 Rows after Cleaning:")
display(df.head())


Missing TotalCharges after conversion: 11

Missing Values after Cleaning:
customerID          0
gender              0
SeniorCitizen       0
Partner             0
Dependents          0
tenure              0
PhoneService        0
MultipleLines       0
InternetService     0
OnlineSecurity      0
OnlineBackup        0
DeviceProtection    0
TechSupport         0
StreamingTV         0
StreamingMovies     0
Contract            0
PaperlessBilling    0
PaymentMethod       0
MonthlyCharges      0
TotalCharges        0
Churn               0
dtype: int64

Dataset Shape after Cleaning: (7043, 21)

First 5 Rows after Cleaning:


customerID  gender  SeniorCitizen Partner Dependents  tenure PhoneService  \
0  7590-VHVEG  Female              0     Yes         No       1           No   
1  5575-GNVDE    Male              0      No         No      34          Yes   
2  3668-QPYBK    Male              0      No         No       2          Yes   
3  7795-CFOCW    Male              0      No         No      45           No   
4  9237-HQITU  Female              0      No         No       2          Yes   

  MultipleLines InternetService OnlineSecurity  ... DeviceProtection  \
0            No             DSL             No  ...               No   
1            No             DSL            Yes  ...              Yes   
2            No             DSL            Yes  ...               No   
3            No             DSL            Yes  ...              Yes   
4            No     Fiber optic             No  ...               No   

  TechSupport StreamingTV StreamingMovies        Contract PaperlessBilling  \
0          No          No              No  Month-to-month              Yes   
1          No          No              No        One year               No   
2          No          No              No  Month-to-month              Yes   
3         Yes          No              No        One year               No   
4          No          No              No  Month-to-month              Yes   

               PaymentMethod MonthlyCharges  TotalCharges  Churn  
0           Electronic check          29.85         29.85     No  
1               Mailed check          56.95       1889.50     No  
2               Mailed check          53.85        108.15    Yes  
3  Bank transfer (automatic)          42.30       1840.75     No  
4           Electronic check          70.70        151.65    Yes  

[5 rows x 21 columns]

## 4. Summary Statistics

In [4]:
# Numerical features
numerical_cols = ['tenure', 'MonthlyCharges', 'TotalCharges']
print("\nNumerical Features Summary:")
display(df[numerical_cols].describe())

# Categorical features
categorical_cols = [col for col in df.columns if col not in numerical_cols + ['customerID']]
print("\nCategorical Features Value Counts:")
for col in categorical_cols:
    print(f"\n{col}:")
    print(df[col].value_counts(normalize=True))


Numerical Features Summary:


tenure  MonthlyCharges  TotalCharges
count  7043.000000     7043.000000   7043.000000
mean     32.371149       64.761692   2279.734304
std      24.559481       30.090047   2266.794470
min       0.000000       18.250000      0.000000
25%       9.000000       35.500000    398.550000
50%      29.000000       70.350000   1394.550000
75%      55.000000       89.850000   3786.600000
max      72.000000      118.750000   8684.800000


Categorical Features Value Counts:

gender:
gender
Male      0.504756
Female    0.495244
Name: proportion, dtype: float64

SeniorCitizen:
SeniorCitizen
0    0.837853
1    0.162147
Name: proportion, dtype: float64

Partner:
Partner
No     0.516967
Yes    0.483033
Name: proportion, dtype: float64

Dependents:
Dependents
No     0.700412
Yes    0.299588
Name: proportion, dtype: float64

PhoneService:
PhoneService
Yes    0.903166
No     0.096834
Name: proportion, dtype: float64

MultipleLines:
MultipleLines
No     0.578163
Yes    0.421837
Name: proportion, dtype: float64

InternetService:
InternetService
Fiber optic    0.439585
DSL            0.343746
No             0.216669
Name: proportion, dtype: float64

OnlineSecurity:
OnlineSecurity
No     0.713332
Yes    0.286668
Name: proportion, dtype: float64

OnlineBackup:
OnlineBackup
No     0.655119
Yes    0.344881
Name: proportion, dtype: float64

DeviceProtection:
DeviceProtection
No     0.656112
Yes    0.343888
Name: proportion, dtype: floa

## 5. Univariate Analysis

In [5]:
# Numerical features: Histograms
for col in numerical_cols:
    fig = px.histogram(df, x=col, title=f'Distribution of {col}', marginal='box')
    fig.show()

# Categorical features: Bar plots
for col in categorical_cols:
    fig = px.histogram(df, x=col, title=f'Distribution of {col}', histnorm='percent')
    fig.update_layout(xaxis_title=col, yaxis_title='Percentage')
    fig.show()

# Churn distribution: Pie chart
fig = px.pie(df, names='Churn', title='Churn Distribution')
fig.show()


## 6. Bivariate Analysis

In [7]:
# Numerical vs. Churn: Box plots
for col in numerical_cols:
    fig = px.box(df, x='Churn', y=col, title=f'{col} by Churn')
    fig.show()

# Categorical vs. Churn: Stacked bar plots
for col in categorical_cols:
    if col != 'Churn':
        temp = df.groupby([col, 'Churn']).size().unstack().fillna(0)
        temp = temp.div(temp.sum(axis=1), axis=0) * 100
        fig = go.Figure(data=[
            go.Bar(name='No', x=temp.index, y=temp['No']),
            go.Bar(name='Yes', x=temp.index, y=temp['Yes'])
        ])
        fig.update_layout(barmode='stack', title=f'Churn by {col}', xaxis_title=col, yaxis_title='Percentage')
        fig.show()

# Numerical vs. Numerical: Scatter plot
fig = px.scatter(df, x='tenure', y='MonthlyCharges', color='Churn', size='TotalCharges',
                 title='tenure vs. MonthlyCharges by Churn')
fig.show()


## 7. Feature Relationships and Interactions

In [9]:
# Cell 2: Code - Correlation heatmap, 3D scatter plot, and categorical interactions
# Correlation heatmap for numerical features
corr = df[numerical_cols].corr()
fig = px.imshow(corr, text_auto=True, title='Correlation Heatmap of Numerical Features')
fig.show()

# 3D scatter plot for numerical features
fig = px.scatter_3d(df, x='tenure', y='MonthlyCharges', z='TotalCharges', color='Churn',
                    title='3D Scatter Plot: tenure, MonthlyCharges, TotalCharges by Churn')
fig.show()

# Grouped bar plots for categorical interactions
interactions = [
    ('InternetService', 'OnlineSecurity'),
    ('Contract', 'PaymentMethod'),
    ('InternetService', 'MonthlyCharges'),
    ('Contract', 'tenure')
]

for col1, col2 in interactions:
    if col2 in numerical_cols:
        # Categorical vs. Numerical
        fig = px.box(df, x=col1, y=col2, color='Churn', title=f'{col2} by {col1} and Churn')
        fig.show()
    else:
        # Categorical vs. Categorical
        temp = df.groupby([col1, col2, 'Churn']).size().unstack().fillna(0)
        temp = temp.div(temp.sum(axis=1), axis=0) * 100
        fig = go.Figure()
        for churn in ['No', 'Yes']:
            for val2 in df[col2].unique():
                fig.add_trace(go.Bar(
                    x=temp.index.levels[0],
                    y=temp.xs(val2, level=1)[churn],
                    name=f'{col2}={val2}, Churn={churn}'
                ))
        fig.update_layout(barmode='group', title=f'Churn by {col1} and {col2}',
                          xaxis_title=col1, yaxis_title='Percentage')
        fig.show()

# Pair plot for numerical features
fig = px.scatter_matrix(df, dimensions=numerical_cols, color='Churn',
                        title='Pair Plot of Numerical Features by Churn')
fig.show()


## 8. Statistical Tests

In [11]:
# Chi-square tests for categorical features vs. Churn
print("\nChi-square Tests for Categorical Features vs. Churn:")
for col in categorical_cols:
    if col != 'Churn':
        contingency = pd.crosstab(df[col], df['Churn'])
        chi2, p, dof, _ = stats.chi2_contingency(contingency)
        print(f"{col}: Chi2={chi2:.2f}, p-value={p:.4f}")

# T-tests for numerical features vs. Churn
print("\nT-tests for Numerical Features vs. Churn:")
for col in numerical_cols:
    churn_yes = df[df['Churn'] == 'Yes'][col]
    churn_no = df[df['Churn'] == 'No'][col]
    t_stat, p_val = stats.ttest_ind(churn_yes, churn_no, nan_policy='omit')
    print(f"{col}: t-stat={t_stat:.2f}, p-value={p_val:.4f}")

# ANOVA for numerical features across categorical features
print("\nANOVA for Numerical Features by Contract:")
for num_col in numerical_cols:
    groups = [df[df['Contract'] == c][num_col] for c in df['Contract'].unique()]
    f_stat, p_val = stats.f_oneway(*groups)
    print(f"{num_col}: F-stat={f_stat:.2f}, p-value={p_val:.4f}")



Chi-square Tests for Categorical Features vs. Churn:
gender: Chi2=0.48, p-value=0.4866
SeniorCitizen: Chi2=159.43, p-value=0.0000
Partner: Chi2=158.73, p-value=0.0000
Dependents: Chi2=189.13, p-value=0.0000
PhoneService: Chi2=0.92, p-value=0.3388
MultipleLines: Chi2=11.14, p-value=0.0008
InternetService: Chi2=732.31, p-value=0.0000
OnlineSecurity: Chi2=205.63, p-value=0.0000
OnlineBackup: Chi2=47.26, p-value=0.0000
DeviceProtection: Chi2=30.51, p-value=0.0000
TechSupport: Chi2=190.17, p-value=0.0000
StreamingTV: Chi2=27.86, p-value=0.0000
StreamingMovies: Chi2=26.25, p-value=0.0000
Contract: Chi2=1184.60, p-value=0.0000
PaperlessBilling: Chi2=258.28, p-value=0.0000
PaymentMethod: Chi2=648.14, p-value=0.0000

T-tests for Numerical Features vs. Churn:
tenure: t-stat=-31.58, p-value=0.0000
MonthlyCharges: t-stat=16.54, p-value=0.0000
TotalCharges: t-stat=-16.98, p-value=0.0000

ANOVA for Numerical Features by Contract:
tenure: F-stat=2960.02, p-value=0.0000
MonthlyCharges: F-stat=20.83, 

## 9. Outlier Detection

In [12]:
# Box plots for numerical features
for col in numerical_cols:
    fig = px.box(df, y=col, title=f'Box Plot of {col}')
    fig.show()

# IQR method for outlier detection
outliers = {}
for col in numerical_cols:
    Q1 = df[col].quantile(0.25)
    Q3 = df[col].quantile(0.75)
    IQR = Q3 - Q1
    lower_bound = Q1 - 1.5 * IQR
    upper_bound = Q3 + 1.5 * IQR
    outlier_count = df[(df[col] < lower_bound) | (df[col] > upper_bound)][col].count()
    outliers[col] = outlier_count
print("\nOutlier Counts:")
for col, count in outliers.items():
    print(f"{col}: {count}")
# Remove outliers


Outlier Counts:
tenure: 0
MonthlyCharges: 0
TotalCharges: 0


## 10. Feature Importance (Preliminary)

In [13]:
# Prepare data for Random Forest
df_encoded = df.copy()
for col in categorical_cols:
    if col != 'Churn':
        le = LabelEncoder()
        df_encoded[col] = le.fit_transform(df_encoded[col])
df_encoded['Churn'] = df_encoded['Churn'].map({'Yes': 1, 'No': 0})

X = df_encoded.drop(['customerID', 'Churn'], axis=1)
y = df_encoded['Churn']

# Train Random Forest
rf = RandomForestClassifier(n_estimators=100, random_state=42)
rf.fit(X, y)

# Feature importance
importance = pd.DataFrame({'Feature': X.columns, 'Importance': rf.feature_importances_})
importance = importance.sort_values('Importance', ascending=False)

# Visualize
fig = px.bar(importance, x='Feature', y='Importance', title='Feature Importance (Random Forest)')
fig.update_layout(xaxis_title='Feature', yaxis_title='Importance', xaxis_tickangle=45)
fig.show()


## 11. Insights and Recommendations

### Key Findings
- **Churn Distribution**: [To be filled based on output, e.g., ~26% churners, indicating class imbalance].
- **Numerical Features**:
  - `tenure`: [e.g., Lower tenure associated with higher churn].
  - `MonthlyCharges`: [e.g., Higher charges linked to churn].
  - `TotalCharges`: [e.g., Correlated with tenure, less direct impact].
- **Categorical Features**:
  - `Contract`: [e.g., Month-to-month contracts have higher churn].
  - `InternetService`: [e.g., Fiber optic users churn more].
  - `PaymentMethod`: [e.g., Electronic check linked to churn].
- **Feature Interactions**:
  - `InternetService` and `OnlineSecurity`: [e.g., Fiber optic without security increases churn].
  - `Contract` and `tenure`: [e.g., Short tenure with month-to-month contracts is risky].
  - `InternetService` and `MonthlyCharges`: [e.g., High charges with fiber optic drive churn].
- **Statistical Tests**:
  - Chi-square: [e.g., Significant associations for `Contract`, `InternetService`].
  - T-tests: [e.g., Significant differences in `MonthlyCharges` by churn].
- **Outliers**: [e.g., Minimal outliers in `MonthlyCharges`, consider capping].
- **Feature Importance**: [e.g., `tenure`, `Contract`, `MonthlyCharges` are top predictors].

### Recommendations for Model Development
- **Feature Selection**:
  - Include high-importance features: `tenure`, `Contract`, `MonthlyCharges`, `InternetService`, `PaymentMethod`.
  - Consider dropping low-impact features: [e.g., `gender` if unimportant].
- **Feature Engineering**:
  - Bin `tenure`: <12, 12-24, >24 months.
  - Create `MonthlyCharges/tenure` ratio to capture cost per month.
  - Count subscribed services (e.g., sum of `OnlineSecurity`, `StreamingTV`).
  - Interaction term: `InternetService_Fiber optic * OnlineSecurity_No`.
- **Class Imbalance**:
  - Use SMOTE or class weights due to [e.g., 26% churners].
- **Preprocessing**:
  - One-hot encode categorical features (`InternetService`, `PaymentMethod`).
  - Normalize numerical features (`tenure`, `MonthlyCharges`, `TotalCharges`).
  - Cap outliers in `MonthlyCharges` and `TotalCharges`.
- **Model Choices**:
  - Test LightGBM, CatBoost for categorical features.
  - Use Random Forest for interpretability.
  - Consider stacking ensemble for performance.

### Next Steps
- Proceed to `Model_Development.ipynb` for preprocessing, feature engineering, and model training.
- Use recommended features and engineering steps.
- Visualize model performance and feature contributions (e.g., SHAP plots).